# Custom Chatbot Project

I have chosen to use web scraping to scrape text from the official cdc website regarding the COVID 19 pandemic. I chose this to get more up to date information regarding the COVID-19 pandemic. While I think there may be sources with more recent dates available, this one is definetly the most reputable from my research. Here is the link: [COVID-19 Timeline](https://www.cdc.gov/museum/timeline/covid19.html)

In [17]:
import openai
openai.api_key = ""
EMBEDDING_MODEL_NAME = "text-embedding-ada-002"
BATCH_SIZE = 100
COMPLETION_MODEL_NAME="gpt-3.5-turbo-instruct"

## Data Wrangling


In [2]:
import requests
from bs4 import BeautifulSoup

In [3]:
def fetch_page(url: str):
    headers = {
    'user-agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/112.0.0.0 Safari/537.36'
    }
    r = requests.get(url, headers=headers)
    if r.status_code == 200:
        return r.text
    else:
        print(r.status_code)
        return r.text

In [4]:
test_url = "https://www.cdc.gov/museum/timeline/covid19.html"
test_result = fetch_page(test_url)
print(test_result)


<!DOCTYPE html>
<html lang="en-us" class="cdc-2022 theme-cyan cdc-page-type-content" >
<head>
	
<!-- Global / universal meta tags -->
<meta charset="utf-8" />
<meta http-equiv="X-UA-Compatible" content="IE=Edge" />
<meta content="width=device-width, initial-scale=1, shrink-to-fit=no" name="viewport" />
<meta name="mobile-web-app-capable" content="yes" />
<meta name="apple-mobile-web-app-capable" content="yes" />
<meta name="theme-color" content="#075290">

<link rel="shortcut icon" href="/TemplatePackage/4.0/assets/imgs/favicon.ico?_=202112">
<link rel="icon" type="image/png" sizes="32x32" href="/TemplatePackage/4.0/assets/imgs/favicon-32x32.png">
<link rel="apple-touch-icon" sizes="60x60" href="/TemplatePackage/4.0/assets/imgs/apple-touch-icon-60x60.png">
<link rel="apple-touch-icon" sizes="180x180" href="/TemplatePackage/4.0/assets/imgs/apple-touch-icon-180x180.png">

<link rel="stylesheet prefetch" href="/TemplatePackage/contrib/libs/bootstrap/latest/css/bootstrap.min.css?_=14204" 

In [5]:
home = "https://www.cdc.gov/museum/timeline/covid19.html"
home_page = fetch_page(home)
soup = BeautifulSoup(home_page, 'html.parser')
divs = soup.find_all('div', class_='card-body')
data=[]
for div in divs:
    date_element = div.find('h5', {'class': 'card-title'})
    text_element = div.find('p')
    if date_element and text_element:
        current_date=date_element.get_text()
        current_text=text_element.get_text()
        data.append(f"{current_date} -- {current_text}")
data

['December 12, 2019 -- A cluster of patients in China’s Hubei Province, in the city of Wuhan, begin to experience the symptoms of an atypical pneumonia-like illness that does not respond well to standard treatments.',
 'December 31, 2019 -- The World Health Organization (WHO) Country Office in China is informed of several cases of a pneumonia of unknown etiology (cause) with symptoms including shortness of breath and fever occurring in Wuhan, China. All initial cases seem connected to the Huanan Seafood Wholesale Market.',
 'January1, 2020 -- The Huanan Seafood Wholesale Market in Wuhan is closed amid worries in China of a reprise of the 2002–2004 SARS (Severe Acute Respiratory Syndrome Coronavirus or SARS-CoV-1) outbreak.',
 'January 2, 2020 -- WHO activates its Incident Management Support Team (IMST) across all three organizational levels: Country Office, Regional Office, and Headquarters.',
 'January 3, 2020 -- China informs WHO that they have identified over 40 cases of pneumonia o

In [6]:
import pandas as pd

pd.set_option('display.max_colwidth', None)  
pd.set_option('display.max_rows', None)  

df = pd.DataFrame(data, columns=['text'])
df

text
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 December 12, 2019 -- A cluster of patients in China’s Hubei Province, in the city of Wuhan, begin to experience the symptoms of an atypical pneumonia-like illness that does not respond well to standard treatments.
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    December 31, 2019 -- The World Health Organization (WHO) Country Office in China is informed of several cases of a pneumonia of unknown etiology (cause) with symptoms including shortness of breath and fever occurring in Wuhan, China. All initial cases seem connected to the Huanan Seafood Wholesale Market.
2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             January1, 2020 -- The Huanan Seafood Wholesale Market in Wuhan is closed amid worries in China of a reprise of the 2002–2004 SARS (Severe Acute Respiratory Syndrome Coronavirus or SARS-CoV-1) outbreak.
3                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               January 2, 2020 -- WHO activates its Incident Management Support Team (IMST) across all three organizational levels: Country Office, Regional Office, and Headquarters.
4                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        January 3, 2020 -- China informs WHO that they have identified ove

## Generating Embeddings


In [7]:


def create_embeddings(input_data, model_name):
    return openai.Embedding.create(
        input=input_data,
        engine=model_name
    )

def extract_embeddings(response):
    return [data["embedding"] for data in response["data"]]

def generate_embeddings(df, batch_size):
    embeddings = []
    for i in range(0, len(df), batch_size):
        response = create_embeddings(df.iloc[i:i+batch_size]["text"].tolist(), EMBEDDING_MODEL_NAME)
        embeddings.extend(extract_embeddings(response))
    return embeddings
# Add embeddings list to dataframe
df["embeddings"] = generate_embeddings(df, BATCH_SIZE)
df

text  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 December 12, 2019 -- A cluster of patients in China’s Hubei Province, in the city of Wuhan, begin to experience the symptoms of an atypical pneumonia-like illness that does not respond well to standard treatments.   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    December 31, 2019 -- The World Health Organization (WHO) Country Office in China is informed of several cases of a pneumonia of unknown etiology (cause) with symptoms including shortness of breath and fever occurring in Wuhan, China. All initial cases seem connected to the Huanan Seafood Wholesale Market.   
2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             January1, 2020 -- The Huanan Seafood Wholesale Market in Wuhan is closed amid worries in China of a reprise of the 2002–2004 SARS (Severe Acute Respiratory Syndrome Coronavirus or SARS-CoV-1) outbreak.   
3                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               January 2, 2020 -- WHO activates its Incident Management Support Team (IMST) across all three organizational levels: Country Office, Regional Office, and Headquarters.   
4                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        January 3, 2020 -- China informs WHO that they have

In [8]:
# save df to csv
df.to_csv("embeddings.csv")

## Custom Query Completion


In [9]:
from openai.embeddings_utils import get_embedding, distances_from_embeddings

def calculate_distances(question_embeddings, df):
    return distances_from_embeddings(
        question_embeddings,
        df["embeddings"].values,
        distance_metric="cosine"
    )

def get_rows_sorted_by_relevance(question, df):
    question_embeddings = get_embedding(question, engine=EMBEDDING_MODEL_NAME)
    df_copy = df.copy()
    df_copy["distances"] = calculate_distances(question_embeddings, df_copy)
    df_copy.sort_values("distances", ascending=True, inplace=True)
    return df_copy

In [10]:
# Testing related text
get_rows_sorted_by_relevance("When did the New York Department of Health say that everyone should wear a mask?", df)

text  \
304                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       July 8, 2022 -- New York Department of Health recommends that all people should wear N95, KN95, or KF94 masks in all public indoor settings and when in crowded outdoor areas due to high community transmission of COVID-19.   
51                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     April 3, 2020 -- At a White House press briefing, CDC announces new mask wearing guidelines and recommends that all people wear a mask when outside of the home.   
286                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              May 3, 2022 -- CDC recommends that everyone continue to wear a mask while in indoor transportation hubs to prevent the spread of COVID-19 – but this is no longer legally enforceable.   
201                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   July 27, 2021 -- Amid a Delta variant surge, CDC releases updated masking guidance recommending that everyone in areas with substantial or high transmission wear a mask indoors.   
93                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   July 14, 2020 -- CDC again calls on all people to wear cloth face masks when leaving their homes to prevent the spread of COVID-19, cal

In [12]:
# Testing related text #2
get_rows_sorted_by_relevance("What age people need to wear a mask?", df)

text  \
304                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       July 8, 2022 -- New York Department of Health recommends that all people should wear N95, KN95, or KF94 masks in all public indoor settings and when in crowded outdoor areas due to high community transmission of COVID-19.   
51                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     April 3, 2020 -- At a White House press briefing, CDC announces new mask wearing guidelines and recommends that all people wear a mask when outside of the home.   
93                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   July 14, 2020 -- CDC again calls on all people to wear cloth face masks when leaving their homes to prevent the spread of COVID-19, calling masks “a critical tool in the fight against COVID-19.”   
201                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   July 27, 2021 -- Amid a Delta variant surge, CDC releases updated masking guidance recommending that everyone in areas with substantial or high transmission wear a mask indoors.   
286                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              May 3, 2022 -- CDC recommends that everyone continue to wear a mask while in indoor transportation hubs to prevent the spre

In [13]:
import tiktoken

def create_prompt(question, df, max_token_count):
    tokenizer = tiktoken.get_encoding("cl100k_base")
    prompt_template = get_prompt_template()
    current_token_count = len(tokenizer.encode(prompt_template)) + len(tokenizer.encode(question))
    context = format_context(question, df, current_token_count, max_token_count, tokenizer)
    return prompt_template.format(context, question)

def get_prompt_template():

    return """
Answer the question based on the context below, and if the question
can't be answered based on the context, say "I don't know"

Context: 

{}



Question: {}
Answer:"""

def format_context(question, df, current_token_count, max_token_count, tokenizer):
    context = []
    for text in get_rows_sorted_by_relevance(question, df)["text"].values:
        text_token_count = len(tokenizer.encode(text))
        current_token_count += text_token_count
        if current_token_count <= max_token_count:
            context.append(text)
        else:
            break
    return "\n\n###\n\n".join(context)

In [14]:
custom_covid_prompt = create_prompt("When did the New York Department of Health say that everyone should wear a mask?", df, 400)
print(custom_covid_prompt)


Answer the question based on the context below, and if the question
can't be answered based on the context, say "I don't know"

Context: 

July 8, 2022 -- New York Department of Health recommends that all people should wear N95, KN95, or KF94 masks in all public indoor settings and when in crowded outdoor areas due to high community transmission of COVID-19.

###

April 3, 2020 -- At a White House press briefing, CDC announces new mask wearing guidelines and recommends that all people wear a mask when outside of the home.

###

May 3, 2022 -- CDC recommends that everyone continue to wear a mask while in indoor transportation hubs to prevent the spread of COVID-19 – but this is no longer legally enforceable.

###

July 27, 2021 -- Amid a Delta variant surge, CDC releases updated masking guidance recommending that everyone in areas with substantial or high transmission wear a mask indoors.

###

July 14, 2020 -- CDC again calls on all people to wear cloth face masks when leaving their h

In [35]:
import openai
def complete_prompt(query, max_prompt_tokens=1800, max_answer_tokens=200):
    try:
        prompt=create_prompt(query, df, max_prompt_tokens)
        response = openai.Completion.create(
            model=COMPLETION_MODEL_NAME,
            prompt=prompt,
            max_tokens=max_answer_tokens
        )
        return response["choices"][0]["text"].strip()
    except Exception as e:
        print(e)
        return ""

In [36]:
def basic_complete_prompt(query, max_prompt_tokens=1800, max_answer_tokens=200):
    response=openai.Completion.create(
    model=COMPLETION_MODEL_NAME,
    prompt=query,
    max_tokens=max_answer_tokens
    )["choices"][0]["text"].strip()
    return response

## Custom Performance Demonstration


### Question 1

In [46]:
print("Basic Completion Model:")
print(basic_complete_prompt("Has the US gone over a million covid deaths? If so when?"))

Basic Completion Model:
As of early December 2021, the US has recorded over 925,000 deaths due to Covid-19. However, the actual number of deaths is likely higher due to unreported or misreported cases. It is possible that the US will reach a million deaths by the end of 2021 if the current trends continue.


In [47]:
print("Custom Query:")
print(complete_prompt("Has the US gone over a million covid deaths? If so when?"))

Custom Query:
Yes, the US has gone over a million COVID-19 deaths. According to the context, the US recorded over 1 million deaths on June 1, 2022.


### Question 2

In [48]:
print("Basic Completion Model:")
print(basic_complete_prompt("What are some updates on omnicron variants"))

Basic Completion Model:
1. Increased transmissibility: The Omicron variant is reported to be more transmissible than previous variants of COVID-19. According to preliminary data, it has a higher reproduction number (R0) than the Delta variant, meaning that it can spread more easily from person to person.

2. Different mutations: The Omicron variant has a significantly higher number of mutations compared to other variants. Some of these mutations are in the spike protein, which is the part of the virus that allows it to enter and infect human cells.

3. Vaccine effectiveness: Initial studies suggest that current COVID-19 vaccines may have reduced effectiveness against the Omicron variant. However, health experts still recommend getting fully vaccinated as it can still provide protection against severe illness and hospitalization.

4. Geographic spread: The Omicron variant was first identified in South Africa and has since been reported in multiple countries around the world. The variant

In [49]:
print("Custom Query:")
print(complete_prompt("What are some updates on omnicron variants"))

Custom Query:
On March 14, 2022, CDC estimated that 23% of all current COVID-19 infections in the U.S. are caused by the Omicron BA.2 subvariant, and on March 26, 2022, CDC estimated that about 55% of all current COVID-19 cases in the U.S. are caused by the Omicron subvariant BA.2. On June 30, 2022, the FDA called for Omicron-specific updates to COVID-19 vaccine boosters from Pfizer-BioNTech and Moderna in fall 2022. Additionally, on December 2, 2021, a second case of the Omicron variant was detected in the U.S. by the Minnesota and the New York City Departments of Health, and on July 6, 2022, CDC data showed that Omicron subvariants BA.4 and BA.5 had become dominant in the U.S., making up over 70
